In [42]:
import geopandas as gpd
import json
import requests
from IPython.display import display
import bispy
from joblib import Parallel, delayed
import jsonschema

gap = bispy.gap.Gap()
bis_utils = bispy.bis.Utils()

In [33]:
us_states = gpd.read_file("https://www2.census.gov/geo/tiger/TIGER2018/STATE/tl_2018_us_state.zip")

In [34]:
us_states

REGION DIVISION STATEFP   STATENS GEOID STUSPS  \
0       3        5      54  01779805    54     WV   
1       3        5      12  00294478    12     FL   
2       2        3      17  01779784    17     IL   
3       2        4      27  00662849    27     MN   
4       3        5      24  01714934    24     MD   
5       1        1      44  01219835    44     RI   
6       4        8      16  01779783    16     ID   
7       1        1      33  01779794    33     NH   
8       3        5      37  01027616    37     NC   
9       1        1      50  01779802    50     VT   
10      1        1      09  01779780    09     CT   
11      3        5      10  01779781    10     DE   
12      4        8      35  00897535    35     NM   
13      4        9      06  01779778    06     CA   
14      1        2      34  01779795    34     NJ   
15      2        3      55  01779806    55     WI   
16      4        9      41  01155107    41     OR   
17      2        4      31  01779792    31     NE   
18      1        2      42  01779798    42     PA   
19      4        9      53  01779804    53     WA   
20      3        7      22  01629543    22     LA   
21      3        5      13  01705317    13     GA   
22      3        6      01  01779775    01     AL   
23      4        8      49  01455989    49     UT   
24      2        3      39  01085497    39     OH   
25      3        7      48  01779801    48     TX   
26      4        8      08  01779779    08     CO   
27      3        5      45  01779799    45     SC   
28      3        7      40  01102857    40     OK   
29      3        6      47  01325873    47     TN   
30      4        8      56  01779807    56     WY   
31      4        9      15  01779782    15     HI   
32      2        4      38  01779797    38     ND   
33      3        6      21  01779786    21     KY   
34      9        0      78  01802710    78     VI   
35      9        0      69  01779809    69     MP   
36      9        0      66  01802705    66     GU   
37      1        1      23  01779787    23     ME   
38      1        2      36  01779796    36     NY   
39      4        8      32  01779793    32     NV   
40      4        9      02  01785533    02     AK   
41      9        0      60  01802701    60     AS   
42      2        3      26  01779789    26     MI   
43      3        7      05  00068085    05     AR   
44      3        6      28  01779790    28     MS   
45      2        4      29  01779791    29     MO   
46      4        8      30  00767982    30     MT   
47      2        4      20  00481813    20     KS   
48      2        3      18  00448508    18     IN   
49      9        0      72  01779808    72     PR   
50      2        4      46  01785534    46     SD   
51      1        1      25  00606926    25     MA   
52      3        5      51  01779803    51     VA   
53      3        5      11  01702382    11     DC   
54      2        4      19  01779785    19     IA   
55      4        8      04  01779777    04     AZ   

                                            NAME LSAD  MTFCC FUNCSTAT  \
0                                  West Virginia   00  G4000        A   
1                                        Florida   00  G4000        A   
2                                       Illinois   00  G4000        A   
3                                      Minnesota   00  G4000        A   
4                                       Maryland   00  G4000        A   
5                                   Rhode Island   00  G4000        A   
6                                          Idaho   00  G4000        A   
7                                  New Hampshire   00  G4000        A   
8                                 North Carolina   00  G4000        A   
9                                        Vermont   00  G4000        A   
10                                   Connecticut   00  G4000        A   
11                                      Delaware   00  G4000        A   
12                              

In [45]:
# Open the file back up and verify
with open("cache/gap.json", "r") as f:
    gap_cache = json.loads(f.read())

In [46]:
gap_cache

[{'processing_metadata': {'status': 'success',
   'date_processed': '2019-08-09T19:49:33.822883',
   'status_message': 'Exact Match',
   'api': "https://www.sciencebase.gov/catalog/items?parentId=527d0a83e4b0850ea0518326&format=json&fields=identifiers,files,webLinks,distributionLinks,dates&filter=itemIdentifier%3D{'key': 'Ursus americanus'}"},
  'parameters': {'Scientific Name': 'Ursus americanus'},
  'GAP Species': {'GAP Habitat Map Item': 'https://www.sciencebase.gov/catalog/item/58fa5f8be4b0b7ea545256a2',
   'GAP Range Map Item': 'https://www.sciencebase.gov/catalog/item/59f5e250e4b063d5d307dde5',
   'GAP Habitat Map WMS': 'https://www.sciencebase.gov/geoserver/CONUS_HabMap_2001/wms?service=WMS&version=1.1.0&request=GetCapabilities',
   'GAP Modeling Database Parameters URL': 'https://www.sciencebase.gov/catalog/file/get/58fa5f8be4b0b7ea545256a2?f=__disk__b1%2F5c%2Fd7%2Fb15cd7a66200aa10973dfe82759c1d21a63bf1a1',
   'GAP ITIS Information URL': 'https://www.sciencebase.gov/catalog/fil

In [36]:
# Tease out the unique GAP species that we were able to find in the entire set of searched names
gap_species = list(map(json.loads,set(map(json.dumps, [r for r in gap_cache if "GAP Species" in r.keys()]))))

In [37]:
gap_species

[{'processing_metadata': {'status': 'success',
   'date_processed': '2019-08-09T19:49:33.822883',
   'status_message': 'Exact Match',
   'api': "https://www.sciencebase.gov/catalog/items?parentId=527d0a83e4b0850ea0518326&format=json&fields=identifiers,files,webLinks,distributionLinks,dates&filter=itemIdentifier%3D{'key': 'Ursus americanus'}"},
  'parameters': {'Scientific Name': 'Ursus americanus'},
  'GAP Species': {'GAP Habitat Map Item': 'https://www.sciencebase.gov/catalog/item/58fa5f8be4b0b7ea545256a2',
   'GAP Range Map Item': 'https://www.sciencebase.gov/catalog/item/59f5e250e4b063d5d307dde5',
   'GAP Habitat Map WMS': 'https://www.sciencebase.gov/geoserver/CONUS_HabMap_2001/wms?service=WMS&version=1.1.0&request=GetCapabilities',
   'GAP Modeling Database Parameters URL': 'https://www.sciencebase.gov/catalog/file/get/58fa5f8be4b0b7ea545256a2?f=__disk__b1%2F5c%2Fd7%2Fb15cd7a66200aa10973dfe82759c1d21a63bf1a1',
   'GAP ITIS Information URL': 'https://www.sciencebase.gov/catalog/fil

In [38]:
gap_box_info=[{'scientific_name':r['GAP Species']['ScientificName'],'common_name':r['GAP Species']['CommonName'],'GAP_SpeciesCode':r['GAP Species']['GAP_SpeciesCode'], 'itis_tsn':r['GAP Species']['itis_tsn_validMatch'], 'range_bounding_box':r['GAP Species']['Range Bounding Box']} for r in gap_species]

In [39]:
gap_box_info

[{'scientific_name': 'Ursus americanus',
  'common_name': 'American Black Bear',
  'GAP_SpeciesCode': 'mABBEx',
  'itis_tsn': '180544',
  'range_bounding_box': [-124.8086117506703,
   25.18362150324615,
   -66.9017614483196,
   49.384366329079675]},
 {'scientific_name': 'Lepidochelys olivacea',
  'common_name': 'Olive Ridley Sea Turtle',
  'GAP_SpeciesCode': 'rORSTx',
  'itis_tsn': '173840',
  'range_bounding_box': [-122.33500661523756,
   32.5292805487602,
   -116.8712004653378,
   37.144612454523866]},
 {'scientific_name': 'Brachylagus idahoensis',
  'common_name': 'Pygmy Rabbit',
  'GAP_SpeciesCode': 'mPYRAx',
  'itis_tsn': '552521',
  'range_bounding_box': [-121.84133312725822,
   36.32490298802412,
   -106.40186585111208,
   48.01114404513639]},
 {'scientific_name': 'Ovis canadensis',
  'common_name': 'Bighorn Sheep',
  'GAP_SpeciesCode': 'mBISHx',
  'itis_tsn': '180711',
  'range_bounding_box': [-121.60586735650045,
   28.971550917166326,
   -102.21362226701393,
   49.00139776081

In [44]:

# Use joblib to run multiple requests for SGCN records in parallel via scientific names
gap_metrics = Parallel(n_jobs=8)(delayed(gap.gap_metrics_species)(us_states, r['GAP_SpeciesCode'], r['range_bounding_box']) for r in gap_box_info)

exception calling callback for <Future at 0x128e58630 state=finished raised BrokenProcessPool>
joblib.externals.loky.process_executor._RemoteTraceback: 
'''
Traceback (most recent call last):
  File "/anaconda3/lib/python3.7/site-packages/joblib/externals/loky/process_executor.py", line 391, in _process_worker
    call_item = call_queue.get(block=True, timeout=timeout)
  File "/anaconda3/lib/python3.7/multiprocessing/queues.py", line 113, in get
    return _ForkingPickler.loads(res)
  File "/anaconda3/lib/python3.7/site-packages/joblib/externals/cloudpickle/cloudpickle.py", line 965, in subimport
    __import__(name)
  File "/anaconda3/lib/python3.7/site-packages/geopandas/__init__.py", line 1, in <module>
    from geopandas.geoseries import GeoSeries
  File "/anaconda3/lib/python3.7/site-packages/geopandas/geoseries.py", line 13, in <module>
    from geopandas.base import GeoPandasBase, _unary_op, _CoordinateIndexer
  File "/anaconda3/lib/python3.7/site-packages/geopandas/base.py", li

BrokenProcessPool: A task has failed to un-serialize. Please ensure that the arguments of the function are all picklable.